In [1]:

import numpy as np
import pandas as pd
import altair as alt
from sklearn.decomposition import PCA
from pathlib import Path
import os
import sklearn.linear_model as lm
from sklearn.preprocessing import add_dummy_feature
from sklearn.metrics import r2_score
alt.data_transformers.disable_max_rows()
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

GDIMoriginal = pd.read_csv('GDIM_2021_09.csv')
GDIMoriginal
EqualityData = pd.read_csv('csvData.csv')
EqualityData.columns
EqualityData=EqualityData.rename(columns={'gendEqal2021':'GEI %', 'econ':'Gender Economic Participation and Opportunity Equality %', 'education':'Gender Education Attainment Equality %', 'health':'Gender Health and Survival Equality %', 'polit':'Gender Political Empowerment'})
region = pd.read_csv('all.csv')
region
#http://info.worldbank.org/governance/wgi/Home/Reports
politicalstability=pd.read_csv('Political_StabilityNoViolence-Table_1.csv')
politicalstability=politicalstability.rename(columns={'Country/Territory':'country'})
politicalstability=pd.melt(politicalstability, id_vars=['country'], value_vars=['1996', '1998', '2000', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020'])
politicalstability=politicalstability.rename(columns={'variable':'year', 'value':'Political Instability Estimate'})
politicalstability
#https://www.worlddata.info/iq-by-country.php
IQ=pd.read_csv('IQ_data_-_Sheet1.csv')
IQ
#https://raw.githubusercontent.com/lukes/ISO-3166-Countries-with-Regional-Codes/master/all/all.csv
#https://worldpopulationreview.com/country-rankings/gender-equality-by-country
region.head()
region=region.rename(columns={'name':'country'})
region['country'] = region['country'].replace(['United Kingdom of Great Britain and Northern Ireland'],'United Kingdom')
region['country'] = region['country'].replace(['United States of America'],'United States')
region['country'] = region['country'].replace(['Bolivia (Plurinational State of)'],'Bolivia')
region['country'] = region['country'].replace(['Viet Nam'],'Vietnam')
region=region[['country','sub-region']]
EqualityData.head()
os.getcwd()
#joining the two data sets
GDIMjoined=GDIMoriginal.join(EqualityData.set_index('country'), on='country')
GDIMjoined=GDIMjoined.join(region.set_index('country'), on='country')
GDIMoriginal['year']=GDIMoriginal['year'].astype(int)
politicalstability['year']=politicalstability['year'].astype(int)
GDIMjoined = GDIMjoined.merge(politicalstability, on=['country', 'year'])
GDIMjoined = GDIMjoined.merge(IQ, on=['country'])
GDIMjoined

#total in politcal instability estimate that are null
GDIMjoined['Political Instability Estimate'].isnull().sum()

#CAT = measure of absolute mobility

#ICSED = International Standard Classification of Education (ISCED): less than primary
#(ISCED 0), primary (ISCED 1), lower secondary (ISCED 2), upper secondary or postsecondary
#non-tertiary (ISCED 3–4), and tertiary (ISCED 5–8). The categories refer to the highest educational
#level completed by the respondent.7

# Dropping columns that won't be used
GDIMdropped=GDIMjoined.drop(['code','year','region','COR','YOS','MIX','MLD_psu','incgroup2','incgroup3','fragile','survey','status','cohort','obs','P1', 'P2', 'P3', 'P4', 'P5', 'C1', 'C2', 'C3', 'C4', 'C5', 'BETA', 'MU050' ,'BHQ4','Q4Q4' , 'BHQ1', 'BHQ2', 'BHQ3', 'Q4BH', 'Q4child','CAT_ISCED5678'], axis=1
                           ).rename(columns ={'region_noHICgroup':'region'})

GDIM=GDIMdropped.dropna()

GDIMdropped.corr()



#Grouped by Region of world
GDIM.groupby('sub-region').mean().reset_index()
GDIM.loc[GDIM['child']=='daughter'].groupby('sub-region').mean().reset_index()
GDIM.loc[GDIM['child']=='son'].groupby('sub-region').mean().reset_index()

#seperation of sexes of children
daughterGDIM=GDIM.loc[GDIM['child']=='daughter']
sonGDIM=GDIM.loc[GDIM['child']=='son']
allGDIM=GDIM.loc[GDIM['child']=='all']
#________________________________________________
#seperation of sexes for children and parents
daughterGDIMdad=daughterGDIM.loc[GDIM['parent']=='dad']
daughterGDIMmom=daughterGDIM.loc[GDIM['parent']=='mom']
daughterGDIMavg=daughterGDIM.loc[GDIM['parent']=='avg']

sonGDIMdad=sonGDIM.loc[GDIM['parent']=='dad']
sonGDIMmom=sonGDIM.loc[GDIM['parent']=='mom']
sonGDIMavg=sonGDIM.loc[GDIM['parent']=='avg']

allGDIMdad=allGDIM.loc[GDIM['parent']=='dad']
allGDIMmom=allGDIM.loc[GDIM['parent']=='mom']
allGDIMavg=allGDIM.loc[GDIM['parent']=='avg']

In [2]:
region.head()

country       sub-region
0     Afghanistan    Southern Asia
1   Åland Islands  Northern Europe
2         Albania  Southern Europe
3         Algeria  Northern Africa
4  American Samoa        Polynesia

In [3]:
GDIM.head()

country      region   incgroup4 parent     child     MEANp     MEANc       SDp       SDc       CAT       DIF  CAT_ISCED0  CAT_ISCED1  CAT_ISCED2  CAT_ISCED34  GEI %  Gender Economic Participation and Opportunity Equality %  Gender Education Attainment Equality %  Gender Health and Survival Equality %  Gender Political Empowerment     sub-region  Political Instability Estimate  IQ  Average Income (USD)  Education expenditure\nper inhabitant (USD)  Daily maximum\ntemperature Celsius
0  Afghanistan  South Asia  Low income    avg       all  2.480162  5.582401  3.809782  5.857765  0.414355  3.203298    0.329975    0.633108    0.584747     0.542553  0.444                                               0.18                                          0.514                                  0.952                         0.132  Southern Asia                            -2.5  80                 340.0                                         13.0                                  24
1  Afghanistan  South Asia  Low income    avg  daughter  2.989992  4.331731  4.010379  5.902685  0.283075  1.433388    0.174239    0.509354    0.445407     0.474830  0.444                                               0.18                                          0.514                                  0.952                         0.132  Southern Asia                            -2.5  80                 340.0                                         13.0                                  24
2  Afghanistan  South Asia  Low income    avg       son  2.353979  5.891941  3.748495  5.806141  0.446874  3.641724    0.364921    0.664005    0.630444     0.563892  0.444                                               0.18                                          0.514                                  0.952                         0.132  Southern Asia                            -2.5  80                 340.0                                         13.0                                  24
3  Afghanistan  South Asia  Low income    dad       all  3.756049  5.538275  5.493762  5.842035  0.350244  2.110216    0.342107    0.731783    0.366321     0.260787  0.444                                               0.18                                          0.514                                  0.952                         0.132  Southern Asia                            -2.5  80                 340.0                                         13.0                                  24
4  Afghanistan  South Asia  Low income    dad  daughter  4.520877  4.277768  5.804775  5.869737  0.230126  0.128818    0.189864    0.819140    0.233389     0.202416  0.444                                               0.18                                          0.514                                  0.952                         0.132  Southern Asia                            -2.5  80                 340.0                                         13.0                                  24

In [4]:
GDIM['Gender Education Attainment Equality %'].max

<bound method NDFrame._add_numeric_operations.<locals>.max of 0       0.514
1       0.514
2       0.514
3       0.514
4       0.514
        ...  
3873    0.938
3874    0.938
3875    0.938
3876    0.938
3877    0.938
Name: Gender Education Attainment Equality %, Length: 3249, dtype: float64>

In [5]:
GDIM.loc[:, 'country':].isna().sum().reset_index().rename(columns={'index': 'variable', 0: 'missing values'})

variable  missing values
0                                             country               0
1                                              region               0
2                                           incgroup4               0
3                                              parent               0
4                                               child               0
5                                               MEANp               0
6                                               MEANc               0
7                                                 SDp               0
8                                                 SDc               0
9                                                 CAT               0
10                                                DIF               0
11                                         CAT_ISCED0               0
12                                         CAT_ISCED1               0
13                                         CAT_ISCED2               0
14                                        CAT_ISCED34               0
15                                              GEI %               0
16  Gender Economic Participation and Opportunity ...               0
17             Gender Education Attainment Equality %               0
18              Gender Health and Survival Equality %               0
19                       Gender Political Empowerment               0
20                                         sub-region               0
21                     Political Instability Estimate               0
22                                                 IQ               0
23                               Average Income (USD)               0
24        Education expenditure\nper inhabitant (USD)               0
25                 Daily maximum\ntemperature Celsius               0

In [6]:
pop_plot = alt.Chart(daughterGDIM).mark_bar().encode(
    x = alt.X('incgroup4:N',sort='-y'), y = alt.Y('MEANc', scale = alt.Scale(zero = False))
).properties(width = 150,height = 200)
#.facet(column = 'incgroup4')

layereddaughter=alt.layer(pop_plot, data=daughterGDIM).facet(column= 'parent')



layereddaughter

alt.FacetChart(...)

In [7]:
#there is an obvious increase in 

In [8]:

pop_plot = alt.Chart(sonGDIM).mark_bar().encode(
    x = alt.X('incgroup4:N', sort='-y'), y = alt.Y('MEANc', scale = alt.Scale(zero = False))
).properties(width = 150,height = 200)
#.facet(column = 'incgroup4')

layeredson=alt.layer(pop_plot, data=sonGDIM).facet(column= 'parent')



layeredson

alt.FacetChart(...)

In [9]:
pop_plot = alt.Chart(allGDIM).mark_bar().encode(
    x = alt.X('incgroup4:N', sort='-y'), 
    y = alt.Y('MEANc', scale = alt.Scale(zero = False))
).properties(width = 150,height = 200)
#.facet(column = 'incgroup4')

layeredall=alt.layer(pop_plot, data=allGDIM).facet(column= 'parent')



layeredall

alt.FacetChart(...)

In [15]:
pop_plot = alt.Chart(allGDIM).mark_bar().encode(
    x = alt.X('incgroup4:N', sort='-y'), 
    y = alt.Y('MEANc', scale = alt.Scale(zero = False)),
    color = alt.Color('region')
).properties(width = 150,height = 200)
#.facet(column = 'incgroup4')

layeredall=alt.layer(pop_plot, data=allGDIM).facet(column= 'parent')



layeredall

#use this in analysis 

alt.FacetChart(...)

In [11]:
GDIMsubregion=GDIM.groupby('sub-region').mean().reset_index()

In [12]:
GDIMsubregion=GDIM.groupby('sub-region').mean().reset_index()
pop_plot = alt.Chart(GDIMsubregion).mark_bar().encode(
    x = alt.X('sub-region:N', sort='-y'), y = alt.Y('MEANc', scale = alt.Scale(zero = False))
).properties(width = 150,height = 200)
#.facet(column = 'incgroup4')

layeredall=alt.layer(pop_plot, data=GDIMsubregion).facet(column= 'parent')



layeredall

#use this in analysis 

alt.FacetChart(...)

In [16]:
GDIMregion=GDIM.groupby('region').mean().reset_index()

pop_plot = alt.Chart(GDIMregion).mark_bar().encode(
    x = alt.X('region:N', sort='-y'), y = alt.Y('MEANc', scale = alt.Scale(zero = False))
).properties(width = 150,height = 200)
#.facet(column = 'incgroup4')

layeredall=alt.layer(pop_plot, data=GDIMregion).facet(column= 'parent')



layeredall

#use this in analysis 

alt.FacetChart(...)

In [35]:
# store quantitative variables separately

x_mx = GDIM[['MEANc','MEANp','GEI %','Gender Economic Participation and Opportunity Equality %','Political Instability Estimate','IQ','Average Income (USD)','Education expenditure\nper inhabitant (USD)','Daily maximum\ntemperature Celsius']]
corr_mx = x_mx.corr()

In [36]:
# correlation between education and other variables
corr_mx.loc[:, 'MEANc'].sort_values()


Daily maximum\ntemperature Celsius                         -0.639200
Education expenditure\nper inhabitant (USD)                 0.554930
Gender Economic Participation and Opportunity Equality %    0.568098
Average Income (USD)                                        0.579955
GEI %                                                       0.585827
Political Instability Estimate                              0.639322
IQ                                                          0.695332
MEANp                                                       0.864336
MEANc                                                       1.000000
Name: MEANc, dtype: float64

Negatively correlated with Daily maximum\ntemperature Celsiu meaning it tends to vary in opposition with these variables;

Strongly positively correlated with MEANp, and IQ meaning it tends to vary together with these variables most.

In [37]:
# store quantitative variables separately
# correlation matrix
allGDIMavg.head()
allGDIMavg.corr()


# store correlation matrix
corr_mx = x_mx.corr()

# melt to long form
corr_mx_long = corr_mx.reset_index().rename(
    columns = {'index': 'row'}
).melt(
    id_vars = 'row',
    var_name = 'col',
    value_name = 'Correlation'
)

# visualize
heatmap = alt.Chart(corr_mx_long).mark_rect().encode(
    x = alt.X('col', title = '', sort = {'field': 'Correlation', 'order': 'ascending'}),
    y = alt.Y('row', title = '', sort = {'field': 'Correlation', 'order': 'ascending'}),
    color = alt.Color('Correlation', 
                      scale = alt.Scale(scheme = 'blueorange',
                                        domain = (-1, 1), 
                                        type = 'sqrt'),
                     legend = alt.Legend(tickCount = 5))
).properties(width = 200, height = 200)

In [41]:
heatmap

alt.Chart(...)

In [42]:
#PCA 
# center and scale ('normalize')
x_ctr = (x_mx - x_mx.mean())/x_mx.std()
x_ctr


MEANc     MEANp     GEI %  Gender Economic Participation and Opportunity Equality %  Political Instability Estimate        IQ  Average Income (USD)  Education expenditure\nper inhabitant (USD)  Daily maximum\ntemperature Celsius
0    -1.620298 -1.412131 -4.958491                                          -4.937296                              -3.299407 -1.128301             -0.867502                                    -0.779368                            0.544745
1    -2.013146 -1.261906 -4.958491                                          -4.937296                              -3.299407 -1.128301             -0.867502                                    -0.779368                            0.544745
2    -1.523069 -1.449311 -4.958491                                          -4.937296                              -3.299407 -1.128301             -0.867502                                    -0.779368                            0.544745
3    -1.634159 -1.036183 -4.958491                                          -4.937296                              -3.299407 -1.128301             -0.867502                                    -0.779368                            0.544745
4    -2.030096 -0.810821 -4.958491                                          -4.937296                              -3.299407 -1.128301             -0.867502                                    -0.779368                            0.544745
...        ...       ...       ...                                                ...                                    ...       ...                   ...                                          ...                                 ...
3873 -1.694479  0.447177 -0.161787                                           1.210927                               0.552424 -1.967120             -0.852617                                    -0.779368                            1.238434
3874 -1.610862  0.367401 -0.161787                                           1.210927                               0.552424 -1.967120             -0.852617                                    -0.779368                            1.238434
3875 -1.479549 -0.293483 -0.161787                                           1.210927                               0.552424 -1.967120             -0.852617                                    -0.779368                            1.238434
3876 -1.518292 -0.244788 -0.161787                                           1.210927                               0.552424 -1.967120             -0.852617                                    -0.779368                            1.238434
3877 -1.444666 -0.337326 -0.161787                                           1.210927                               0.552424 -1.967120             -0.852617                                    -0.779368                            1.238434

[3249 rows x 9 columns]

In [43]:
# compute principal components
pca = PCA(n_components = x_ctr.shape[1]) 
pca.fit(x_ctr)

PCA(n_components=9)

In [44]:
# variance ratios
pca.explained_variance_ratio_

array([0.65972916, 0.10175267, 0.08467338, 0.05500419, 0.03413347,
       0.03007815, 0.01979817, 0.01210921, 0.00272159])

In [45]:
# store proportion of variance explained as a dataframe
pca_var_explained = pd.DataFrame({'Proportion of variance explained': pca.explained_variance_ratio_})

# add component number as a new column
pca_var_explained['Component'] = np.arange(1, 10)

# print
pca_var_explained.head()

Proportion of variance explained  Component
0                          0.659729          1
1                          0.101753          2
2                          0.084673          3
3                          0.055004          4
4                          0.034133          5

In [46]:
# add component number as a new column
pca_var_explained['Cumulative variance explained'] = pca_var_explained.iloc[:,0].cumsum(axis = 0)

# print
pca_var_explained.head(3)

Proportion of variance explained  Component  Cumulative variance explained
0                          0.659729          1                       0.659729
1                          0.101753          2                       0.761482
2                          0.084673          3                       0.846155

In [47]:
# encode component axis only as base layer
base = alt.Chart(pca_var_explained).encode(
    x = 'Component')

# make a base layer for the proportion of variance explained
prop_var_base = base.encode(
    y = alt.Y('Proportion of variance explained',
              axis = alt.Axis(titleColor = '#57A44C'))
)

# make a base layer for the cumulative variance explained
cum_var_base = base.encode(
    y = alt.Y('Cumulative variance explained', axis = alt.Axis(titleColor = '#5276A7'))
)

# add points and lines to each base layer
prop_var = prop_var_base.mark_line(stroke = '#57A44C') + prop_var_base.mark_point(color = '#57A44C')
cum_var = cum_var_base.mark_line() + cum_var_base.mark_point()

# layer the layers
var_explained_plot = alt.layer(prop_var, cum_var).resolve_scale(y = 'independent')

# display
var_explained_plot

alt.LayerChart(...)

In [48]:
#principal components explain more than 60% of total variation
main = pca_var_explained[pca_var_explained['Proportion of variance explained'] > 0.07].count()

main_pca = main[0] 

#print
main_pca 

3

In [51]:
#How much total variation is captured by these 3 PC
main = pca_var_explained[pca_var_explained['Proportion of variance explained'] > 0.07].sum()
main_variation = main[0]

#print
main_variation

0.8461552156177867

More than 84% of the variation is captured by the first 3 components

In [52]:
corr_mx = x_mx.corr()

# store the loadings as a data frame with appropriate names
loading_df = pd.DataFrame(pca.components_).transpose().rename(
    columns = {0: 'PC1', 1: 'PC2', 2: 'PC3' } # add entries for each selected component
).loc[:, ['PC1', 'PC2', 'PC3']] # slice just components of interest

# add a column with the variable names
loading_df['Variable'] = x_mx.columns.values

# print
loading_df.head()

PC1       PC2       PC3                                           Variable
0 -0.344636 -0.266317  0.339438                                              MEANc
1 -0.331154 -0.263275  0.391683                                              MEANp
2 -0.335637  0.052723 -0.522737                                              GEI %
3 -0.299360 -0.418128 -0.533057  Gender Economic Participation and Opportunity ...
4 -0.345115 -0.069630 -0.220119                     Political Instability Estimate

In [84]:
# melt from wide to long
loading_plot_df = loading_df.melt(
    id_vars = 'Variable',
    var_name = 'Principal Component',
    value_name = 'Loading'
)

# add a column of zeros to encode for x = 0 line to plot
loading_plot_df['zero'] = np.repeat(0, len(loading_plot_df))

# create base layer
base = alt.Chart(loading_plot_df)

# create lines + points for loadings
loadings = base.mark_line(point = True).encode(
    y = alt.X('Variable', title = ''),
    x = 'Loading',
    color = 'Principal Component'
)

# create line at zero
rule = base.mark_rule().encode(x = alt.X('zero', title = 'Loading'), size = alt.value(0.05))

# layer
loading_plot = (loadings + rule).properties(width = 120)

# show
loading_plot

alt.LayerChart(...)

In [85]:
loading_plot.facet('Principal Component')

alt.FacetChart(...)

- PC1 positively influenced by 'Daily maximum\ntemperature Celsius' and negatively influenced by everything else.
- PC2 strongly positively influenced by 'Average Income (USD)',Education expenditure\nper inhabitant (USD)',and 'Gender Political Empowerment' and negatively influenced by 'almost everything else'.
- PC3 strongly positively influenced by 'MEANp','MEANc','IQ' and negatively influenced by 'Gender Health and Survival Equality %', and 'GEI%'.  

Let's call,

PC1 'Temperature'.

PC2: 'Income and educational expenditure'. 

PC3: 'Intelligence'

In [86]:
# three largest variances
x_mx.var().sort_values(ascending = False).head(3)

Average Income (USD)                           2.059727e+08
Education expenditure\nper inhabitant (USD)    8.157467e+05
IQ                                             9.431731e+01
dtype: float64

In [88]:
# project data onto first four components; store as data frame
projected_data = pd.DataFrame(pca.fit_transform(x_ctr)).iloc[:, 0:4].rename(columns = {0: 'PC1', 1: 'PC2', 2: 'PC3', 3: 'PC4'})

# add state and county
projected_data[['country', 'region']] = GDIM[['country', 'region']]

# print
projected_data.head(4)

PC1       PC2       PC3       PC4      country      region
0  6.303645  1.603258  4.402189  0.936198  Afghanistan  South Asia
1  6.388608  1.670018  4.334535  1.016201  Afghanistan  South Asia
2  6.282617  1.586735  4.418933  0.916397  Afghanistan  South Asia
3  6.184111  1.490725  4.531561  0.763821  Afghanistan  South Asia

In [96]:
# base chart
base = alt.Chart(projected_data)

# data scatter
scatter = base.mark_point(opacity = 0.2).encode(
    x = alt.X('PC2:Q', title = 'Income and educational expenditure PC'),
    y = alt.Y('PC3:Q', title = 'Intelligence PC'),
)

# show
scatter

alt.Chart(...)

In [97]:
# find cutoff value
sum = projected_data.PC2 + projected_data.PC3
pc_2plus4 = sorted(sum, reverse = True)

#print
pc_2plus4[0:15]

[6.029556659737264,
 6.026659822535691,
 6.025942853535131,
 6.024752360150519,
 6.0222867996616705,
 6.021687456195749,
 6.005668162334825,
 6.005446959370072,
 6.004553201404099,
 5.986214664274441,
 5.985550831405886,
 5.982618606325863,
 4.212761526313267,
 4.206693835266984,
 4.197299208105598]

In [108]:
# store outlying rows using cutoff
outliers = projected_data[(projected_data.PC2 + projected_data.PC3) > 5]

# plot outliers in red
pts = alt.Chart(outliers).mark_circle(
    color = 'red',
    opacity = 0.6
).encode(
    x = 'PC2',
    y = 'PC3'
)

# layer
scatter + pts

alt.LayerChart(...)

In [99]:
# base chart
base = alt.Chart(projected_data)

# data scatter
scatter = base.mark_point(opacity = 0.2).encode(
    x = alt.X('PC1:Q', title = 'Temperature PC'),
    y = alt.Y('PC3:Q', title = 'Intelligence PC'),
)

# show
scatter

alt.Chart(...)

In [100]:
# find cutoff value
sum = projected_data.PC1 + projected_data.PC3
pc_2plus4 = sorted(sum, reverse = True)

#print
pc_2plus4[0:15]

[10.73681803672063,
 10.73495826597783,
 10.723142552431792,
 10.717436269895433,
 10.715672391571417,
 10.712639287335314,
 10.711128056103645,
 10.710984282867962,
 10.705834027794412,
 10.701550172490592,
 10.69693949847551,
 10.693727314374513,
 8.25853410906085,
 8.257181897564422,
 8.256506657017196]

In [101]:
# store outlying rows using cutoff
outliers = projected_data[(projected_data.PC1 + projected_data.PC3) > 9]

# plot outliers in red
pts = alt.Chart(outliers).mark_circle(
    color = 'red',
    opacity = 0.6
).encode(
    x = 'PC1',
    y = 'PC3'
)

# layer
scatter + pts

alt.LayerChart(...)

In [109]:
# base chart
base = alt.Chart(projected_data)

# data scatter
scatter = base.mark_point(opacity = 0.2).encode(
    x = alt.X('PC1:Q', title = 'Temperature PC'),
    y = alt.Y('PC2:Q', title = 'Income and educational expenditure PC'),
)

# show
scatter

alt.Chart(...)

In [110]:
# find cutoff value
sum = projected_data.PC1 + projected_data.PC2
pc_2plus4 = sorted(sum, reverse = True)

#print
pc_2plus4[0:15]

[8.367160878966521,
 8.202428716689447,
 8.165134598764528,
 8.05862576627356,
 7.906903725641607,
 7.869352595226984,
 7.780379237938134,
 7.706767560412341,
 7.674836314362732,
 7.6491804471880975,
 7.608388221298998,
 7.5840394047444075,
 7.135643430969217,
 7.102332102629946,
 6.812516704169625]

In [112]:
# store outlying rows using cutoff
outliers = projected_data[(projected_data.PC1 + projected_data.PC2) > 7]

# plot outliers in red
pts = alt.Chart(outliers).mark_circle(
    color = 'red',
    opacity = 0.6
).encode(
    x = 'PC1',
    y = 'PC2'
)

# layer
scatter + pts

alt.LayerChart(...)

In [82]:
y = sonGDIMavg.MEANc.values
x_df = sonGDIMavg[['MEANp','GEI %','Gender Economic Participation and Opportunity Equality %','Political Instability Estimate','IQ','Average Income (USD)','Education expenditure\nper inhabitant (USD)','Daily maximum\ntemperature Celsius']]
x_df.head()

# add column of ones (for intercept)
x_mx = add_dummy_feature(x_df, value = 1)
# fit first model
mlr = lm.LinearRegression(fit_intercept = False)
mlr.fit(x_mx, y)
mlr.coef_

# fitted values and residuals
fitted = mlr.predict(x_mx)
resid = y - fitted
# error variance estimate
n, p = x_mx.shape
sigmasqhat = resid.var()*(n - 1)/(n - p)
sigmasqhat

xtx = x_mx.transpose().dot(x_mx) # X'X
xtxinv = np.linalg.inv(xtx) # (X'X)^{-1}
vhat = sigmasqhat*xtxinv # V
vhat

coef_se = np.sqrt(vhat.diagonal()) # (v_jj)^{1/2}
coef_se

# using sklearn.metrics.r2_score
r2_score(y, fitted)

0.8099759519090262

In [83]:
y = allGDIMavg.MEANc.values
x_df = allGDIMavg[['MEANp','GEI %','Gender Economic Participation and Opportunity Equality %','Political Instability Estimate','IQ','Average Income (USD)','Education expenditure\nper inhabitant (USD)','Daily maximum\ntemperature Celsius']]
x_df.head()

# add column of ones (for intercept)
x_mx = add_dummy_feature(x_df, value = 1)
# fit first model
mlr = lm.LinearRegression(fit_intercept = False)
mlr.fit(x_mx, y)
mlr.coef_

# fitted values and residuals
fitted = mlr.predict(x_mx)
resid = y - fitted
# error variance estimate
n, p = x_mx.shape
sigmasqhat = resid.var()*(n - 1)/(n - p)
sigmasqhat

xtx = x_mx.transpose().dot(x_mx) # X'X
xtxinv = np.linalg.inv(xtx) # (X'X)^{-1}
vhat = sigmasqhat*xtxinv # V
vhat

coef_se = np.sqrt(vhat.diagonal()) # (v_jj)^{1/2}
coef_se

# using sklearn.metrics.r2_score
r2_score(y, fitted)

0.8256482972372444

In [84]:
y = daughterGDIMmom.MEANc.values
x_df = daughterGDIMmom[['MEANp','GEI %','Gender Economic Participation and Opportunity Equality %','Political Instability Estimate','IQ','Average Income (USD)','Education expenditure\nper inhabitant (USD)','Daily maximum\ntemperature Celsius']]
x_df.head()

# add column of ones (for intercept)
x_mx = add_dummy_feature(x_df, value = 1)
# fit first model
mlr = lm.LinearRegression(fit_intercept = False)
mlr.fit(x_mx, y)
mlr.coef_

# fitted values and residuals
fitted = mlr.predict(x_mx)
resid = y - fitted
# error variance estimate
n, p = x_mx.shape
sigmasqhat = resid.var()*(n - 1)/(n - p)
sigmasqhat

xtx = x_mx.transpose().dot(x_mx) # X'X
xtxinv = np.linalg.inv(xtx) # (X'X)^{-1}
vhat = sigmasqhat*xtxinv # V
vhat

coef_se = np.sqrt(vhat.diagonal()) # (v_jj)^{1/2}
coef_se

# using sklearn.metrics.r2_score
r2_score(y, fitted)

0.8245853488380321

In [85]:
y = daughterGDIMdad.MEANc.values
x_df = daughterGDIMdad[['MEANp','GEI %','Gender Economic Participation and Opportunity Equality %','Political Instability Estimate','IQ','Average Income (USD)','Education expenditure\nper inhabitant (USD)','Daily maximum\ntemperature Celsius']]
x_df.head()

# add column of ones (for intercept)
x_mx = add_dummy_feature(x_df, value = 1)
# fit first model
mlr = lm.LinearRegression(fit_intercept = False)
mlr.fit(x_mx, y)
mlr.coef_

# fitted values and residuals
fitted = mlr.predict(x_mx)
resid = y - fitted
# error variance estimate
n, p = x_mx.shape
sigmasqhat = resid.var()*(n - 1)/(n - p)
sigmasqhat

xtx = x_mx.transpose().dot(x_mx) # X'X
xtxinv = np.linalg.inv(xtx) # (X'X)^{-1}
vhat = sigmasqhat*xtxinv # V
vhat

coef_se = np.sqrt(vhat.diagonal()) # (v_jj)^{1/2}
coef_se

# using sklearn.metrics.r2_score
r2_score(y, fitted)

0.8013826281279788

In [86]:
y = sonGDIMdad.MEANc.values
x_df = sonGDIMdad[['MEANp','GEI %','Gender Economic Participation and Opportunity Equality %','Political Instability Estimate','IQ','Average Income (USD)','Education expenditure\nper inhabitant (USD)','Daily maximum\ntemperature Celsius']]
x_df.head()

# add column of ones (for intercept)
x_mx = add_dummy_feature(x_df, value = 1)
# fit first model
mlr = lm.LinearRegression(fit_intercept = False)
mlr.fit(x_mx, y)
mlr.coef_

# fitted values and residuals
fitted = mlr.predict(x_mx)
resid = y - fitted
# error variance estimate
n, p = x_mx.shape
sigmasqhat = resid.var()*(n - 1)/(n - p)
sigmasqhat

xtx = x_mx.transpose().dot(x_mx) # X'X
xtxinv = np.linalg.inv(xtx) # (X'X)^{-1}
vhat = sigmasqhat*xtxinv # V
vhat

coef_se = np.sqrt(vhat.diagonal()) # (v_jj)^{1/2}
coef_se

# using sklearn.metrics.r2_score
r2_score(y, fitted)

0.812311593567588

In [87]:
y = sonGDIMmom.MEANc.values
x_df = sonGDIMmom[['MEANp','GEI %','Gender Economic Participation and Opportunity Equality %','Political Instability Estimate','IQ','Average Income (USD)','Education expenditure\nper inhabitant (USD)','Daily maximum\ntemperature Celsius']]
x_df.head()

# add column of ones (for intercept)
x_mx = add_dummy_feature(x_df, value = 1)
# fit first model
mlr = lm.LinearRegression(fit_intercept = False)
mlr.fit(x_mx, y)
mlr.coef_

# fitted values and residuals
fitted = mlr.predict(x_mx)
resid = y - fitted
# error variance estimate
n, p = x_mx.shape
sigmasqhat = resid.var()*(n - 1)/(n - p)
sigmasqhat

xtx = x_mx.transpose().dot(x_mx) # X'X
xtxinv = np.linalg.inv(xtx) # (X'X)^{-1}
vhat = sigmasqhat*xtxinv # V
vhat

coef_se = np.sqrt(vhat.diagonal()) # (v_jj)^{1/2}
coef_se

# using sklearn.metrics.r2_score
r2_score(y, fitted)

0.8202405465662264